In [1]:
import os
from nltk.corpus import RegexpTokenizer,stopwords

In [2]:
folder_name = r'C:\Users\mohit\Desktop\IIIT Delhi\2nd Sem\Information Retrieval\Assignments\1\Q3\data'
file_list = os.listdir(folder_name)

In [3]:
print(f'Total number of files : {len(file_list)}')

Total number of files : 1400


In [4]:
# This would be the document structure we would be using for postings list
# This is the sample data structure
data_structure = {'word':['document_frequency', {'document_number':['no_of_occurences', ['positions_in_the_document']]}]}

In [5]:
def find_occurences(word_list,word):
    occurences = [index+1 for index in range(len(word_list)) if word_list[index]==word]
    return len(occurences),occurences

In [6]:
positional_index = {}

for file_index in range(len(file_list)):

    f = open(f'{folder_name}/{file_list[file_index]}', 'r')
    all_words = f.read().split()

    file_number = file_index + 1
  
    unique_words=list(set(all_words))

    for unique_word in unique_words:
        no_of_occurences,indices = find_occurences(all_words,unique_word)
    
        if unique_word in positional_index.keys():
            positional_index[unique_word][0] = positional_index[unique_word][0] + 1
            document_level_data_structure = positional_index[unique_word][1]
            document_level_data_structure[file_number] = [no_of_occurences,indices]
        else:
            positional_index[unique_word] = [1,{file_number:[no_of_occurences,indices]}]

In [7]:
import pickle

pickle.dump(positional_index,open('positional_index.pkl','wb'))
positional_index = pickle.load(open('positional_index.pkl','rb'))

In [8]:
for i in positional_index:
    print(i, positional_index[i], "\n\n")

spanwise [27, {1: [1, [14]], 189: [1, [76]], 205: [1, [137]], 284: [1, [16]], 433: [1, [47]], 513: [1, [46]], 674: [1, [16]], 677: [1, [84]], 678: [1, [22]], 679: [1, [20]], 682: [3, [41, 48, 82]], 696: [4, [9, 36, 127, 151]], 699: [2, [42, 105]], 710: [1, [31]], 783: [1, [40]], 794: [2, [53, 117]], 877: [1, [22]], 918: [1, [29]], 919: [1, [63]], 1064: [4, [56, 79, 99, 105]], 1197: [3, [26, 69, 84]], 1220: [2, [38, 106]], 1280: [3, [41, 59, 112]], 1289: [1, [77]], 1320: [1, [26]], 1332: [2, [2, 13]], 1334: [2, [2, 12]]}] 


showed [40, {1: [1, [46]], 17: [1, [59]], 174: [1, [95]], 177: [1, [62]], 189: [2, [87, 133]], 212: [1, [121]], 216: [1, [18]], 244: [1, [58]], 261: [1, [41]], 508: [1, [44]], 623: [1, [74]], 635: [1, [43]], 643: [1, [42]], 646: [1, [72]], 686: [1, [78]], 690: [1, [38]], 713: [1, [58]], 717: [1, [136]], 782: [1, [110]], 816: [2, [46, 58]], 859: [3, [57, 75, 133]], 984: [1, [45]], 986: [1, [43]], 988: [1, [37]], 993: [2, [61, 112]], 996: [1, [62]], 1006: [1, [41]], 1

### Querying based on positional index

In [9]:
positional_index['dissociating']

[9,
 {110: [3, [2, 43, 50]],
  166: [2, [44, 79]],
  167: [2, [3, 11]],
  236: [1, [69]],
  317: [1, [4]],
  517: [1, [50]],
  575: [1, [9]],
  656: [1, [10]],
  1295: [2, [4, 45]]}]

In [10]:
def preprocess_input_query(input_query):
    stop_words = set(stopwords.words('english'))
    input_query = input_query.lower()
    updated_word_list = input_query.split()
    token = RegexpTokenizer(r"\w+")
    updated_word_list = token.tokenize(' '.join(updated_word_list))
    input_query = ' '.join(updated_word_list)
    input_query = input_query.split(" ")
    input_tokens = [word for word in input_query if word not in stop_words]

    return input_tokens

In [11]:
def intersection_of_multiple_list(l):
    final_list = []

    for i in l:
        if final_list == []:
            final_list=set(i)
        else:
            final_list = set(final_list).intersection(set(i))
    
    return sorted(list(final_list))

In [12]:
def doc_position_list_of_tokens(l1,l2):
    n1=len(l1)
    n2=len(l2)
    i=0
    j=0

    resultant_list = []

    while i<n1 and j<n2:
        if l1[i] + 1 == l2[j]:
            resultant_list.append(l2[j])
            i+=1
            j+=1
        elif l1[i] > l2[j]:
            j+=1
        elif l1[i] < l2[j]:
            i+=1
    
    return resultant_list

In [13]:
def print_postional_index_query_results(document_dict, i):
    
    document_list = [file_list[doc-1] for doc in document_dict.keys()]
    
    print(f'\nNumber of documents retrieved for query {i} query using positional index is {len(document_dict)}')
    if len(document_dict.keys()) > 0:
        print(f'Names of documents retrieved for query {i} query using positional index is {document_list}')
    else:
        print(f'Number of documents retrieved for query {i} query using positional index is {len(document_dict)}')
    print("\n")

In [14]:
#input_query = "dissociating gas"
#input_query = "dissociating gas lucid"
#input_query = "dissociating diatomic gas"
#input_query = "dissociating gas characterized"

In [15]:
bigram_index = {}


for file in file_list:
    
    s = []
    
    f = open(f'{folder_name}/{file}','r')
    file_contents = f.read()
    
    words = list(file_contents.split(" "))
    
    for i in range(len(words)-1):
        s.append(words[i]+" "+words[i+1])
    
    for i in s:
        if i in bigram_index:
            val = bigram_index[i]
            val[0]+=1
            val[1].append(file)
            bigram_index[i] = val
            
        else:
            bigram_index[i] = [1, [file]]

    f.close()

        
for i in bigram_index:
    print(i, bigram_index[i], "\n\n")

experimental investigation [54, ['cranfield0001', 'cranfield0029', 'cranfield0084', 'cranfield0084', 'cranfield0170', 'cranfield0173', 'cranfield0176', 'cranfield0189', 'cranfield0245', 'cranfield0251', 'cranfield0372', 'cranfield0372', 'cranfield0423', 'cranfield0442', 'cranfield0442', 'cranfield0497', 'cranfield0505', 'cranfield0522', 'cranfield0552', 'cranfield0569', 'cranfield0635', 'cranfield0636', 'cranfield0662', 'cranfield0694', 'cranfield0713', 'cranfield0766', 'cranfield0772', 'cranfield0801', 'cranfield0816', 'cranfield0836', 'cranfield0844', 'cranfield0858', 'cranfield0887', 'cranfield0932', 'cranfield0986', 'cranfield0996', 'cranfield1019', 'cranfield1039', 'cranfield1074', 'cranfield1092', 'cranfield1097', 'cranfield1098', 'cranfield1156', 'cranfield1156', 'cranfield1159', 'cranfield1161', 'cranfield1205', 'cranfield1220', 'cranfield1225', 'cranfield1227', 'cranfield1230', 'cranfield1231', 'cranfield1338', 'cranfield1364']] 


investigation aerodynamics [1, ['cranfield000

explanations advanced [1, ['cranfield0315']] 


advanced cases [1, ['cranfield0315']] 


cases discrepancies [1, ['cranfield0315']] 


discrepancies occur [1, ['cranfield0315']] 


occur several [1, ['cranfield0315']] 


uncertainties difficulties [1, ['cranfield0315']] 


difficulties arise [1, ['cranfield0315']] 


arise fixing [1, ['cranfield0315']] 


discussed illustrated [1, ['cranfield0315']] 


illustrated examples [1, ['cranfield0315']] 


examples particular [1, ['cranfield0315']] 


particular special [1, ['cranfield0315']] 


special care [2, ['cranfield0315', 'cranfield1251']] 


care needed [1, ['cranfield0315']] 


needed interpreting [1, ['cranfield0315']] 


interpreting results [1, ['cranfield0315']] 


obtained transition [1, ['cranfield0315']] 


transition fixed [4, ['cranfield0315', 'cranfield0315', 'cranfield0794', 'cranfield0798']] 


fixed low [1, ['cranfield0315']] 


numbers say [1, ['cranfield0315']] 


say less [1, ['cranfield0315']] 


less r [1, ['cranfie

located towards [1, ['cranfield0811']] 


towards rear [1, ['cranfield0811']] 


rear fuselage [2, ['cranfield0811', 'cranfield0911']] 


fuselage rule [1, ['cranfield0811']] 


rule states [1, ['cranfield0811']] 


states shock [1, ['cranfield0811']] 


aircraft carrying [1, ['cranfield0811']] 


lift equal [1, ['cranfield0811']] 


equal shock [1, ['cranfield0811']] 


volume neglecting [1, ['cranfield0811']] 


neglecting lift [1, ['cranfield0811']] 


lift neglecting [1, ['cranfield0811']] 


neglecting volume [1, ['cranfield0811']] 


volume whichever [1, ['cranfield0811']] 


whichever greater [1, ['cranfield0811']] 


greater chart [1, ['cranfield0811']] 


chart presented [1, ['cranfield0811']] 


rapid estimates [1, ['cranfield0811']] 


made shock [4, ['cranfield0811', 'cranfield1222', 'cranfield1313', 'cranfield1391']] 


noise lifting [1, ['cranfield0811']] 


lifting wingbody [1, ['cranfield0811']] 


investigation two [1, ['cranfield0812']] 


two bluff [1, ['cranfield081

600 conditions [1, ['cranfield1289']] 


conditions calculations [1, ['cranfield1289']] 


numbers reducedfrequency [1, ['cranfield1289']] 


10 direct [1, ['cranfield1289']] 


moments forms [1, ['cranfield1289']] 


forms suitable [1, ['cranfield1289']] 


suitable inserted [1, ['cranfield1289']] 


inserted equations [1, ['cranfield1289']] 


motion used [1, ['cranfield1289']] 


calculation dynamic [1, ['cranfield1289']] 


dynamic responses [1, ['cranfield1289']] 


responses flexible [1, ['cranfield1289']] 


flexible lifting [1, ['cranfield1289']] 


vehicles random [1, ['cranfield1289']] 


random turbulence [1, ['cranfield1289']] 


turbulence compared [1, ['cranfield1289']] 


results methods [2, ['cranfield1289', 'cranfield1320']] 


transonic flutter [5, ['cranfield1290', 'cranfield1290', 'cranfield1290', 'cranfield1338', 'cranfield1338']] 


characteristics 45 [1, ['cranfield1290']] 


planform air [1, ['cranfield1290']] 


freon12 langley [1, ['cranfield1290']] 


langley

In [16]:
pickle.dump(bigram_index,open('bigram_index.pkl','wb'))
bigram_index = pickle.load(open('bigram_index.pkl','rb'))

In [17]:
print(len(positional_index))
print(len(bigram_index))

8996
85209


As we can see here, there are 8996 unique words in the case of positional index. This is because if the word is occuring in multiple files, those will be updated.

But in the case of bigram inverted index, there are 85209 entries. this makes sense because we look for all the bigrams. there are more number of bigrams existing in the file

In [18]:
n = int(input("Enter number of phrase queries to execute:"))
print(n, "\n")
query_no=1
while n>0:
    input_query = input("Enter the input phrase query: ")
        
    input_tokens = preprocess_input_query(input_query)

    doc_indices_of_tokens = []
    positional_indices_of_tokens = []
    
    bigram_query_docs = []
    
    for i in range(len(input_tokens)-1):
        word = input_tokens[i]+" "+input_tokens[i+1]
        
        intersection = []
        if word in bigram_index:
            #print(word, " occur in ", bigram_index[word][0], " documents and the documents are ", bigram_index[word][1], "\n\n")
            intersection.append(bigram_index[word][1])
            
    print("Number of documents retrieved for query ", 3-n, " using bigram inverted index: ", len(intersection))
    if len(intersection)!=0:
        print("Names of documents retrieved for query ", 3-n, " using bigram inverted index: ", list(set.intersection(*map(set,intersection))))
    else:
        print("Names of documents retrieved for query ", 3-n, " using bigram inverted index: ", [])
    #print("Theese words occur together in ", list(set.intersection(*map(set,intersection))))
    

    for token in input_tokens:
            if token in positional_index.keys():
                doc_indices_of_tokens.append(list(positional_index[token][1].keys()))
                positional_indices_of_tokens.append(positional_index[token][1])

    common_documents = intersection_of_multiple_list(doc_indices_of_tokens)

    relevant_doc_ids = {}

    for doc in common_documents:

        resultant_list = []
        for i in range(len(positional_indices_of_tokens)):
            if resultant_list==[]:
                resultant_list = positional_indices_of_tokens[i][doc][1]
            else:
                resultant_list = doc_position_list_of_tokens(resultant_list,positional_indices_of_tokens[i][doc][1])
            
            if len(resultant_list)==0:
                continue
            
        if len(resultant_list)>0:
            relevant_doc_ids[doc] = len(resultant_list)

        
    relevant_doc_ids = dict(sorted(relevant_doc_ids.items(),reverse=True,key=lambda x:x[1]))
    print_postional_index_query_results(relevant_doc_ids,query_no)
    
    query_no+=1
    
    n-=1

Enter number of phrase queries to execute:2
2 

Enter the input phrase query: dissociating in a gas
Number of documents retrieved for query  1  using bigram inverted index:  1
Names of documents retrieved for query  1  using bigram inverted index:  ['cranfield0517', 'cranfield0656', 'cranfield0167', 'cranfield0575', 'cranfield1295', 'cranfield0317', 'cranfield0166', 'cranfield0110']

Number of documents retrieved for query 1 query using positional index is 8
Names of documents retrieved for query 1 query using positional index is ['cranfield0110', 'cranfield0166', 'cranfield0167', 'cranfield0317', 'cranfield0517', 'cranfield0575', 'cranfield0656', 'cranfield1295']


Enter the input phrase query: dissociating in a gas for lucid
Number of documents retrieved for query  2  using bigram inverted index:  1
Names of documents retrieved for query  2  using bigram inverted index:  ['cranfield0110']

Number of documents retrieved for query 2 query using positional index is 1
Names of documents 